In [1]:
print("hello")

hello


In [2]:
%%bash

pip install --upgrade pip
pip install farm-haystack[colab,inference]


Defaulting to user installation because normal site-packages is not writeable
  Obtaining dependency information for pip from https://files.pythonhosted.org/packages/47/6a/453160888fab7c6a432a6e25f8afe6256d0d9f2cbd25971021da6491d899/pip-23.3.1-py3-none-any.whl.metadata
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.1/2.1 MB 144.4 kB/s eta 0:00:0000:0100:01
  Attempting uninstall: pip
    Found existing installation: pip 23.2.1
    Uninstalling pip-23.2.1:
      Successfully uninstalled pip-23.2.1
Defaulting to user installation because normal site-packages is not writeable


In [3]:
from haystack.document_stores import InMemoryDocumentStore

document_store = InMemoryDocumentStore(use_bm25=True)


/home/pushkar/.local/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [4]:
import os
from haystack.pipelines.standard_pipelines import TextIndexingPipeline
doc_dir = "IIITB_crawled_files"

files_to_index = [doc_dir + "/" + f for f in os.listdir(doc_dir)]
indexing_pipeline = TextIndexingPipeline(document_store)
indexing_pipeline.run_batch(file_paths=files_to_index)


Preprocessing:   0%|          | 0/71 [00:00<?, ?docs/s]We found one or more sentences whose word count is higher than the split length.
Document 2240cd1fd4d06bff60cd5a315c258e84 is 18230 characters long after preprocessing, where the maximum length should be 10000. Something might be wrong with the splitting, check the document affected to prevent issues at query time. This document will be now hard-split at 10000 chars recursively.
Document 7e548d17c514fe39ea8484cf5d77444f is 11691 characters long after preprocessing, where the maximum length should be 10000. Something might be wrong with the splitting, check the document affected to prevent issues at query time. This document will be now hard-split at 10000 chars recursively.
Document dfb8f8d2383d161e384330a2ddcb8c69 is 24967 characters long after preprocessing, where the maximum length should be 10000. Something might be wrong with the splitting, check the document affected to prevent issues at query time. This document will be now 

{'documents': [<Document: {'content': '{"content": "\\n\\n\\n\\n\\u00a0\\n\\n\\n \\n  \\n  \\n  \\n  \\n  Networking\\n  and Communication Lab (NCL) \\n  \\u00a0\\n  \\n \\n\\n\\n\\n\\n\\n\\n\\n\\n\\n\\n\\n\\n\\n\\n\\n\\n\\n\\n\\u00a0\\n\\n\\n\\n\\n \\n  \\n  \\n  More details on Open Calls for Fellowship Applications, click here\\n  \\n  More\\n  details on workshop, click here\\n  \\n  \\n  Networking and Communication Lab. (NCL) in IIIT-Bangalore mainly focuses on\\n  various R&D areas related to broadband wireless network. Recent major\\n  areas of work include Power Saving in devices and base stations by New\\n  Protocols, multi-Radio Access Technology (RAT selection), Cognitive Radio,\\n  TVWS, scheduling schemes in LTE-A and Beyond, MAC for IoT devices as well as\\n  secured Transport layer. This lab was created in Jan. 2007 by research fund\\n  from Hewlett Packard, Motorola India Research Labs. Later on the Lab received\\n  research funding from Microsoft, Nokia, Intel, Siemen

In [5]:
from haystack.nodes import BM25Retriever

retriever = BM25Retriever(document_store=document_store)


In [6]:
from haystack.nodes import FARMReader

reader = FARMReader(model_name_or_path="deepset/roberta-base-squad2", use_gpu=True)


In [7]:
from haystack.pipelines import ExtractiveQAPipeline

pipe = ExtractiveQAPipeline(reader, retriever)


In [16]:
prediction = pipe.run(
    query="Campus size of IIITB ?", params={"Retriever": {"top_k": 10}, "Reader": {"top_k": 5}}
)


Inferencing Samples:   0%|          | 0/3 [00:00<?, ? Batches/s]

Inferencing Samples: 100%|██████████| 3/3 [00:00<00:00,  6.31 Batches/s]


In [17]:
from haystack.utils import print_answers

print_answers(prediction, details="minimum")  ## Choose from `minimum`, `medium`, and `all`



'Query: Campus size of IIITB ?'
'Answers:'
[   {   'answer': 'nine-acre',
        'context': ' pre-seed and seed-stage investments.\\u00a0\\n Campus and '
                   'Location: The nine-acre main campus in Electronic City, '
                   'the heart of the IT Industry in Benga'},
    {   'answer': 'u00a9 2023',
        'context': '                \\n            \\n        \\n    \\n    '
                   '\\n    \\n        \\n            \\n                '
                   '\\n                    \\u00a9 2023 IIIT Bangalore. '},
    {   'answer': '+91 80 4140 7777/ 2852 7627',
        'context': '                      '
                   'Telephone:\\n                            +91 80 4140 7777/ '
                   '2852 7627\\n                        '
                   '\\n                                 '},
    {   'answer': 'Largely organized and run by academic departments and '
                  'students, the events provide multiple ways to connect.',
   